In [6]:
import pandas as pd

df_corpus = pd.read_json("hf://datasets/mteb/quora/corpus.jsonl", lines=True)

df_queries = pd.read_json("hf://datasets/mteb/quora/queries.jsonl", lines=True)

splits = {'dev': 'qrels/dev.jsonl', 'test': 'qrels/test.jsonl'}
df_qrels_dev = pd.read_json("hf://datasets/mteb/quora/" + splits["dev"], lines=True)
df_qrels_test = pd.read_json("hf://datasets/mteb/quora/" + splits["test"], lines=True)

## 数据集分析

In [7]:
df_queries

_id                                               text
0         318                How does Quora look to a moderator?
1         378  How do I refuse to chose between different thi...
2         379  Did Ben Affleck shine more than Christian Bale...
3         399  What are the effects of demonitization of 500 ...
4         420                       Why creativity is important?
...       ...                                                ...
14995  537630  How can I drink 12 beers as fast as possible w...
14996  537660                How did different races come about?
14997  537730             How do I get more friends on Facebook?
14998  537793  Can I take my 14 year old son to the Global Ci...
14999  537876  How do Russian politics and geostrategy affect...

[15000 rows x 2 columns]

In [17]:
df_qrels_test

query-id  corpus-id  score
0            46     134031      1
1            46     271267      1
2            46     134030      1
3           187     144864      1
4           187     202157      1
...         ...        ...    ...
15670    537630     537629      1
15671    537660     537661      1
15672    537730     537729      1
15673    537793     537792      1
15674    537876     537875      1

[15675 rows x 3 columns]

In [30]:
df_corpus

_id title                                               text
0            1        What is the step by step guide to invest in sh...
1            2        What is the step by step guide to invest in sh...
2            3        What is the story of Kohinoor (Koh-i-Noor) Dia...
3            4        What would happen if the Indian government sto...
4            5        How can I increase the speed of my internet co...
...        ...   ...                                                ...
522926  537929                                        What's this coin?
522927  537930        What is the approx annual cost of living while...
522928  537931        I am having little hairfall problem but I want...
522929  537932                    What is like to have sex with cousin?
522930  537933            What is it like to have sex with your cousin?

[522931 rows x 3 columns]

In [22]:
df_qrels_test['score'].value_counts()

score
1    15675
Name: count, dtype: int64

In [11]:
df_qrels_dev['query-id'].value_counts()

query-id
80779     84
11167     50
106721    34
399       28
12508     24
          ..
1166       1
975        1
548        1
420        1
378        1
Name: count, Length: 5000, dtype: int64

In [25]:
df_qrels = pd.concat([df_qrels_dev, df_qrels_test])
df_qrels

query-id  corpus-id  score
0           318        317      1
1           378        377      1
2           379      29976      1
3           379        380      1
4           379      45646      1
...         ...        ...    ...
15670    537630     537629      1
15671    537660     537661      1
15672    537730     537729      1
15673    537793     537792      1
15674    537876     537875      1

[23301 rows x 3 columns]

## 数据集处理

### 分组方案一
- query当作条件
- 第二个参数叫group,存放所有的相似句子对

一共会产出?条数据

In [37]:
df_corpus_rn = df_corpus[['_id', 'text']].rename(columns={"_id": "corpus-id","text": "corpus"})
print(df_corpus_rn)
df_queries_rn = df_queries[['_id', 'text']].rename(columns={"_id": "query-id","text": "query"})
print(df_queries_rn)

df__qerl_final = df_qrels.merge(df_corpus_rn, on='corpus-id').merge(df_queries_rn, on='query-id')
df__qerl_final

        corpus-id                                             corpus
0               1  What is the step by step guide to invest in sh...
1               2  What is the step by step guide to invest in sh...
2               3  What is the story of Kohinoor (Koh-i-Noor) Dia...
3               4  What would happen if the Indian government sto...
4               5  How can I increase the speed of my internet co...
...           ...                                                ...
522926     537929                                  What's this coin?
522927     537930  What is the approx annual cost of living while...
522928     537931  I am having little hairfall problem but I want...
522929     537932              What is like to have sex with cousin?
522930     537933      What is it like to have sex with your cousin?

[522931 rows x 2 columns]
       query-id                                              query
0           318                How does Quora look to a moderator?
1          

query-id  corpus-id  score  \
0           318        317      1   
1           378        377      1   
2           379      29976      1   
3           379        380      1   
4           379      45646      1   
...         ...        ...    ...   
23296    537630     537629      1   
23297    537660     537661      1   
23298    537730     537729      1   
23299    537793     537792      1   
23300    537876     537875      1   

                                                  corpus  \
0      What does the Quora website look like to membe...   
1      Is it possible to pursue many different things...   
2      According to you, whose Batman performance was...   
3      No fanboys please, but who was the true batman...   
4      Who do you think portrayed Batman better: Chri...   
...                                                  ...   
23296  How can I drink 12 beers as fast as possible w...   
23297  How did humans turn into different races of pe...   
23298         How can someone get more Facebook friends?   
23299  Can I take my 14 year old son to the Global Ci...   
23300  How does Russian politics affect Australia and...   

                                                   query  
0                    How does Quora look to a moderator?  
1      How do I refuse to chose between different thi...  
2      Did Ben Affleck shine more than Christian Bale...  
3      Did Ben Affleck shine more than Christian Bale...  
4      Did Ben Affleck shine more than Christian Bale...  
...                                                  ...  
23296  How can I drink 12 beers as fast as possible w...  
23297                How did different races come about?  
23298             How do I get more friends on Facebook?  
23299  Can I take my 14 year old son to the Global Ci...  
23300  How do Russian politics and geostrategy affect...  

[23301 rows x 5 columns]

In [39]:
name_group_list = [(name[0], group) for name, group in df__qerl_final.groupby(['query-id'])]
print(len(name_group_list))
print(len(name_group_list[0][1]))
print(name_group_list[1][1])
print(len(name_group_list[1][1]))

print()

name_group_list_filter = list(filter(lambda _: len(_[1]) > 1, name_group_list))
print(len(name_group_list_filter))
print(len(name_group_list_filter[0][1]))
print(name_group_list_filter[1][1])
print(len(name_group_list_filter[1][1]))

15000
3
      query-id  corpus-id  score  \
7629       187     144864      1   
7630       187     202157      1   
7631       187      68733      1   
7632       187      68732      1   
7633       187     394711      1   
7634       187     394712      1   
7635       187        188      1   

                                                 corpus  \
7629                          Why do I have nightmares?   
7630                          Why do we get Nightmares?   
7631            What are the main causes of nightmares?   
7632  Why do we have nightmares? What is the cause o...   
7633               What do you think causes bad dreams?   
7634                         Why do we have bad dreams?   
7635             What causes nightmares that seem real?   

                         query  
7629  What causes a nightmare?  
7630  What causes a nightmare?  
7631  What causes a nightmare?  
7632  What causes a nightmare?  
7633  What causes a nightmare?  
7634  What causes a nightmare?  

In [40]:

print(name_group_list_filter[1])

(187,       query-id  corpus-id  score  \
7629       187     144864      1   
7630       187     202157      1   
7631       187      68733      1   
7632       187      68732      1   
7633       187     394711      1   
7634       187     394712      1   
7635       187        188      1   

                                                 corpus  \
7629                          Why do I have nightmares?   
7630                          Why do we get Nightmares?   
7631            What are the main causes of nightmares?   
7632  Why do we have nightmares? What is the cause o...   
7633               What do you think causes bad dreams?   
7634                         Why do we have bad dreams?   
7635             What causes nightmares that seem real?   

                         query  
7629  What causes a nightmare?  
7630  What causes a nightmare?  
7631  What causes a nightmare?  
7632  What causes a nightmare?  
7633  What causes a nightmare?  
7634  What causes a nightmare?  
7

In [45]:
name_group_list_filter[0][1]['corpus'].tolist()

['What are good questions to ask on Quora?',
 'Why should I ask Quora?',
 "What's the best question to ask in Quora?"]

In [47]:
def handle(row):
    # query_id = row[0]
    cond = row[1]['query'].tolist()[0]
    group = row[1]['corpus'].tolist()
    return (cond, group)


# print(handle({"_id":"dev_query1", "text":"生产过后怎么还有一层肚子"}))


In [48]:
result = list(map(handle, name_group_list_filter))

In [50]:
result_df = pd.DataFrame(result, columns=['condition', 'group'])
result_df

condition  \
0                 Which question should I ask on Quora?   
1                              What causes a nightmare?   
2     If I do not monetize YouTube videos & upload c...   
3     Did Ben Affleck shine more than Christian Bale...   
4     What are the effects of demonitization of 500 ...   
...                                                 ...   
3444                              Who invented the bra?   
3445  What are the ways that India and Pakistan can ...   
3446  Can the president replace the vice president w...   
3447                      Why do golf Ball have dimple?   
3448      What is natural selection? Why does it occur?   

                                                  group  
0     [What are good questions to ask on Quora?, Why...  
1     [Why do I have nightmares?, Why do we get Nigh...  
2     [Can I upload part of anime videos on YouTube ...  
3     [According to you, whose Batman performance wa...  
4     [How does demonetization of the 500 and 1000 n...  
...                                                 ...  
3444  [When and why was bra invented?, When was the ...  
3445  [How can there be everlasting peace between In...  
3446  [Can the President fire the Vice President?, C...  
3447  [Why do regulation golf balls have dimples?, W...  
3448  [What are the best ways to explain evolution b...  

[3449 rows x 2 columns]

In [51]:
result_df = result_df.dropna()
result_df

condition  \
0                 Which question should I ask on Quora?   
1                              What causes a nightmare?   
2     If I do not monetize YouTube videos & upload c...   
3     Did Ben Affleck shine more than Christian Bale...   
4     What are the effects of demonitization of 500 ...   
...                                                 ...   
3444                              Who invented the bra?   
3445  What are the ways that India and Pakistan can ...   
3446  Can the president replace the vice president w...   
3447                      Why do golf Ball have dimple?   
3448      What is natural selection? Why does it occur?   

                                                  group  
0     [What are good questions to ask on Quora?, Why...  
1     [Why do I have nightmares?, Why do we get Nigh...  
2     [Can I upload part of anime videos on YouTube ...  
3     [According to you, whose Batman performance wa...  
4     [How does demonetization of the 500 and 1000 n...  
...                                                 ...  
3444  [When and why was bra invented?, When was the ...  
3445  [How can there be everlasting peace between In...  
3446  [Can the President fire the Vice President?, C...  
3447  [Why do regulation golf balls have dimples?, W...  
3448  [What are the best ways to explain evolution b...  

[3449 rows x 2 columns]

In [52]:
! pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 20.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.9/183.9 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 12.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 14.3 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.2
    Uninstalling fsspec-2025.3.2:
      Successfully uninstalled fsspec-2025.3.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torch 2.6.0+cu124 requires nvidia-cublas-cu12==12.4.5.8; platform_system == "Linux" and platform_machine == "x86_64", but you have nvidia-cublas-cu12 12.5.3.2 which is incompatible.
torch 2.6.0+cu124 requires nvidia-cuda-cupti-cu12==12.4.127; platform_system =

In [53]:
from datasets import Dataset, DatasetDict
from sklearn.model_selection import train_test_split
from huggingface_hub import login, create_repo

In [54]:
# 转换为Hugging Face Dataset
dataset = Dataset.from_pandas(result_df)

# 划分数据集
# 首先划分训练集和临时集 (80% train, 20% temp)
train_df, temp_df = train_test_split(result_df, test_size=0.2, random_state=42)

# 然后从临时集中划分验证集和测试集 (50% dev, 50% test)
dev_df, test_df = train_test_split(temp_df, test_size=0.5, random_state=42)

# 转换为Dataset对象
train_dataset = Dataset.from_pandas(train_df)
dev_dataset = Dataset.from_pandas(dev_df)
test_dataset = Dataset.from_pandas(test_df)

# 创建DatasetDict
dataset_dict = DatasetDict({
    "train": train_dataset,
    "validation": dev_dataset,
    "test": test_dataset
})


In [55]:
from google.colab import userdata
userdata.get('HF_TOKEN')

login(token=userdata.get('HF_TOKEN'))

# 创建数据集仓库
repo_id = "bcai001/c-sts-quora-query-as-condition-group-as-pos"  # 例如: "johnsmith/sentiment-analysis-data"
create_repo(repo_id, repo_type="dataset", exist_ok=True)

# 上传数据集
dataset_dict.push_to_hub(repo_id, private=True)

print(f"Dataset uploaded to: https://huggingface.co/datasets/{repo_id}")


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/3 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Dataset uploaded to: https://huggingface.co/datasets/bcai001/c-sts-quora-query-as-condition-group-as-pos
